In [12]:
%pip install tqdm transformers pandas pyarrow torch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 755.5/755.5 MB 3.8 MB/s eta 0:00:0000:0100:01
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached triton-2.2.0-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (167.9 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached Jinja2-3.1.3-py3-none-any.whl (133 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (99 kB)
  Using cached sympy-1.12-py3-none-any.whl (5.7 MB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cach

In [13]:
import glob
import torch
import os
import re
import shutil
from tqdm import tqdm
from transformers import AutoTokenizer, AutoModelForCausalLM
import pandas as pd

In [14]:
model_name = "Dans-DiscountModels/Dans-StructureEvaluator-Small"

In [15]:
model = AutoModelForCausalLM.from_pretrained(model_name, device_map = "cuda")
tokenizer = AutoTokenizer.from_pretrained(model_name)

RuntimeError: Failed to import transformers.models.mistral.modeling_mistral because of the following error (look up to see its traceback):
module 'torch._subclasses' has no attribute 'functional_tensor'

In [51]:
def calculate_perplexity(text):
    input_ids = torch.tensor([tokenizer.encode(text)]).to("cuda:0")

    model.eval()

    with torch.no_grad():
        outputs = model(input_ids, labels=input_ids)
        loss = outputs[0]

    del outputs
    torch.cuda.empty_cache()

    return torch.exp(loss).item()

In [57]:
def split_data_into_windows(data):
    lines = data.splitlines()
    windows = []

    for i in range(1, len(lines)):
        # Get the previous line and current line
        prev_line = lines[i - 1]
        curr_line = lines[i]

        # If it's the first line or the last line, don't split it
        if i == 1:
            mid_index = len(curr_line) // 2
            first_half = curr_line[:mid_index]
            windows.append((prev_line, first_half))
        elif i == len(lines) - 1:
            mid_index = len(prev_line) // 2
            second_half = prev_line[mid_index:]
            windows.append((second_half, curr_line))
        else:
            # Split the current line into two halves
            curr_mid_index = len(curr_line) // 2
            prev_mid_index = len(prev_line) // 2
            first_half = curr_line[:curr_mid_index]
            second_half = prev_line[prev_mid_index:]

            windows.append((second_half, first_half))
    return windows

In [41]:
def join_lines(lines):
    with_space = lines[0] + " " + lines[1]
    without_space = lines[0] + lines[1]
    with_space_perplexity = calculate_perplexity(with_space)
    without_space_perplexity = calculate_perplexity(without_space)
    if with_space_perplexity < without_space_perplexity:
        return with_space
    else:
        return without_space

In [42]:
def join_windows(windows):
    output = ""
    for window in windows:
        output += join_lines(window)
    return output

In [43]:
files = glob.glob("orig/*.txt")

In [44]:
# remove all non-original files that have an original file associated with them
copy_files = {}
for file in files:
    if file in copy_files:
        continue
    if " (_ORIGINAL SERIES)" in file:
        original_file = file.replace(" (_ORIGINAL SERIES)", "")
        copy_files[file] = original_file.replace("orig/", "dedup/")
    elif " (_UNCHANGED)" in file:
        original_file = file.replace(" (_UNCHANGED)", "")
        copy_files[file] = original_file.replace("orig/", "dedup/")
    else:
        copy_files[file] = file.replace("orig/", "dedup/")

# for all values in copy_files, if the value contains parentheses and the filename without them is already a value in copy_files remove it
to_remove = []
for kv in copy_files.items():
    if "(" in kv[1]:
        original_file = re.sub(r" \(.+\)", "", kv[1])
        if original_file in copy_files.values():
            to_remove.append(kv[0])

for file in to_remove:
    del copy_files[file]

for kv in copy_files.items():
    if "+" in kv[1]:
        original_file = re.sub(r" \(.+\)", "", kv[1])
        copy_files[kv[0]] = original_file

to_remove.clear()
for kv in copy_files.items():
    if "(" in kv[1]:
        original_file = re.sub(r" \(.+\)", "", kv[1])
        if original_file in copy_files.values():
            to_remove.append(kv[0])

for file in to_remove:
    del copy_files[file]

for kv in copy_files.items():
    if "(Full)" in kv[1]:
        original_file = re.sub(r" \(.+\)", "", kv[1])
        if original_file not in copy_files.values():
            copy_files[kv[0]] = original_file

to_remove.clear()
for kv in copy_files.items():
    if "(" in kv[1]:
        to_remove.append(kv[0])

for file in to_remove:
    del copy_files[file]

# copy files to new directory
shutil.rmtree("dedup", ignore_errors=True)
os.makedirs("dedup", exist_ok=True)
for kv in copy_files.items():
    shutil.copy(kv[0], kv[1])


In [45]:
files = glob.glob("dedup/*.txt")

In [46]:
# remove all empty lines in the dedup files
shutil.rmtree("dedup_no_empty", ignore_errors=True)
os.makedirs("dedup_no_empty", exist_ok=True)
for file in files:
    with open(file, "r") as f:
        data = f.read()
    while "\n\n" in data:
        data = data.replace("\n\n", "\n")
    new_file = file.replace("dedup", "dedup_no_empty")
    with open(new_file, "w") as f:
        f.write(data)

In [47]:
files = glob.glob("dedup_no_empty/*.txt")

In [60]:
shutil.rmtree("joined", ignore_errors=True)
os.makedirs("joined", exist_ok=True)
for file in tqdm(files):
    with open(file, "r") as f:
        data = f.read()
    windows = split_data_into_windows(data)
    joined = join_windows(windows)
    new_file = file.replace("dedup_no_empty", "joined")
    # in joined make sure there is a space after every period or comma
    joined = joined
    
    with open(new_file, "w") as f:
        f.write(joined)

100%|██████████| 30/30 [01:56<00:00,  3.88s/it]


In [24]:
files = glob.glob("joined/*.txt")

In [26]:
shutil.rmtree("cleaned", ignore_errors=True)
os.makedirs("cleaned", exist_ok=True)
for file in tqdm(files):
    with open(file, "r") as f:
        data = f.read()
    data = data.replace(".", ". ").replace(",", ", ").replace("  ", " ").replace('"', "")
    new_file = file.replace("joined", "cleaned")
    with open(new_file, "w") as f:
        f.write(data)

100%|██████████| 30/30 [00:00<00:00, 8242.44it/s]


In [27]:
files = glob.glob("cleaned/*.txt")

In [29]:
# load each file as a row with the text in a column called text
texts = []
full_text = ""
for file in tqdm(files):
    with open(file, "r") as f:
        data = f.read()
    texts.append(data)
    full_text += data + "\n"

file = "bambisleep.parquet"
df = pd.DataFrame({ "text": texts }, columns=["text"])
df.to_parquet(file)
df

100%|██████████| 30/30 [00:00<00:00, 44779.05it/s]


text
0   Just Bambi Sleep. Deeper and deeper. Feeling b...
1   Every command Bambi has accepted in this sessi...
2   Feeling wonderfully obedient Bambi. Perfectly ...
3   That's right. Doing so well. Like a pretty gir...
4   Bambi is completely susceptible to hypnosis. A...
5   That's right Bambi. Eyelids fluttering like a ...
6   That's right Bambi feeling so good. Just drift...
7   Now as Bambi Sleeps deeper and deeper. Fuzzier...
8   Bambi Sleep Now. And Bambi suddenly finds hers...
9   Bambi is a perfect fuckable fashion puppet. A ...
10  Drifting deeper and deeper Bambi. More and mor...
11  [Various voices looping conditioning phrases]S...
12  Bambi Sleep Now. Just Bambi Sleep. Every time ...
13  Feeling the need to be Primped And Pampered.  ...
14  That's a Good Girl Bambi. Feeling more and mor...
15  And Bambi is so perfectly trapped in her bimbo...
16  And Bambi every time you go so deeply into tra...
17  Bambi Freeze. That's a Good Girl. All thoughts...
18  Such a Good Girl Bambi. Feeling so much pleasu...
19  Soon it will be time for you to awaken Bambi. ...
20  That's right Bambi. Feeling so wonderful. Feel...
21  Take a deep breath Bambi. Hold it for a moment...
22  That's a Good Girl Bambi. Feeling more and mor...
23  Bambi Sleep now. No resistance, must sleep now...
24  Slipping deeper and deeper now Bambi. Just tak...
25  Hi sweetie! Welcome to the Sleepy Girl Salon B...
26  It's time to go so much deeper Bambi. And ther...
27  That's right. Deeply asleep now Bambi. Complet...
28  Bambi can feel her perfect heaving titties now...
29  That's it Bambi. So peaceful. So perfect. So b...

In [30]:
end_tokenizer = AutoTokenizer.from_pretrained("TinyLlama/TinyLlama-1.1B-Chat-v1.0")

tokenizer_config.json: 100%|██████████| 1.29k/1.29k [00:00<00:00, 9.67MB/s]
tokenizer.model: 100%|██████████| 500k/500k [00:00<00:00, 5.74MB/s]
tokenizer.json: 100%|██████████| 1.84M/1.84M [00:00<00:00, 4.03MB/s]
special_tokens_map.json: 100%|██████████| 551/551 [00:00<00:00, 4.15MB/s]


In [31]:
len(end_tokenizer.tokenize(full_text))

Token indices sequence length is longer than the specified maximum sequence length for this model (77787 > 2048). Running this sequence through the model will result in indexing errors


['▁Just',
 '▁B',
 'amb',
 'i',
 '▁S',
 'leep',
 '.',
 '▁De',
 'eper',
 '▁and',
 '▁deeper',
 '.',
 '▁Fe',
 'eling',
 '▁better',
 '▁and',
 '▁better',
 '.',
 '▁Because',
 '▁every',
 '▁time',
 '▁B',
 'amb',
 'i',
 '▁he',
 'ars',
 '▁the',
 '▁words',
 '.',
 '▁Good',
 '▁Girl',
 '.',
 '▁Her',
 '▁pleasure',
 '▁deep',
 'ens',
 '.',
 '▁Fe',
 'eling',
 '▁so',
 '▁much',
 '▁better',
 '.',
 '▁So',
 '▁much',
 '▁more',
 '▁relax',
 'ed',
 '▁and',
 '▁happy',
 '.',
 '▁Fe',
 'eling',
 '▁so',
 '▁good',
 '▁all',
 '▁over',
 '.',
 '▁Str',
 'ong',
 'er',
 '▁and',
 '▁stronger',
 '.',
 '▁More',
 '▁and',
 '▁more',
 '▁wonder',
 'fully',
 '▁eu',
 'ph',
 'or',
 'ic',
 '.',
 '▁Such',
 '▁a',
 '▁Good',
 '▁Girl',
 '.',
 '▁Happy',
 '.',
 '▁Rel',
 'ax',
 'ed',
 '▁and',
 '▁accepting',
 '.',
 '▁Fe',
 'eling',
 '▁that',
 '▁deep',
 '▁wave',
 '▁of',
 '▁capt',
 'iv',
 'ating',
 '▁pleasure',
 '▁and',
 '▁ob',
 'ed',
 'ience',
 '.',
 '▁Even',
 '▁more',
 '▁bl',
 'iss',
 'ful',
 '▁with',
 '▁every',
 '▁trigger',
 '.',
 '▁M',
 'aking',